# Woche xx: Wir bauen einen Filter

## Warum bauen wir einen Filter in T-SQL?

Manchmal möchte man im Backend eine Stored Procedure haben die Daten an eine Anwendung wie beispielsweise ein ASP.NET Core Webanwendung gefiltert zurückliefert. In der Regel wird so ein Filter, wenn es nicht gerade eine Unzahl an Werten sind die gefiltert werden sollen in der Benutzeroberfläche als Combobox dargestellt. Um einen möglichst komfortablen Filter zu haben müssen drei Stati abgedeckt werden:

- In der Combobox ist nichts ausgewählt, d.h. der Filter ist nicht aktiv, es werden alle Datensätze zurückgegeben
- Es ist ein Wert ausgewählt, d.h. es müssen alle Daten zurückgegeben werden bei denen im entsprechenden Feld der ausgewählte Wert enthalten ist
- Es sind mehrere Werte ausgewählt, d.h. es müssen alle Datensätze ausgewählt werden bei denen im spezifischen Feld einer der angegebenen Werte enthalten ist. 

Damit es nicht zu einfach wird haben wir in unserer Anwendung möglicherweise mehr als einen Filter, d.h. es müssen mehere Felder entsprechend der übergebenen Werte gefiltert werden. 

## Wie sieht unser Setup aus?

Wie immer arbeiten wir mit der Wide World Importers Standard-Datenbank, genauer mit der Tabelle `Application.Countries`. Diese Tabelle enthält eine Liste mit Ländern die auch noch einem Kontinent zugeordnet sind, die wiederum einer Region zugeordnet sind. Damit können wir doch arbeiten.

In [1]:
SELECT
	 CountryID
   , CountryName
   , FormalName
   , IsoAlpha3Code
   , IsoNumericCode
   , CountryType
   , LatestRecordedPopulation
   , Continent
   , Region
   , Subregion
   , Border
   , LastEditedBy
   , ValidFrom
   , ValidTo
FROM Application.Countries;

(190 rows affected)

Total execution time: 00:00:00.691

CountryID CountryName FormalName IsoAlpha3Code IsoNumericCode CountryType LatestRecordedPopulation Continent Region Subregion Border LastEditedBy ValidFrom ValidTo 1 Afghanistan Islamic State of Afghanistan AFG 4 UN Member State 28400000 Asia Asia Southern Asia 0xE610000001049A01000066666666A69D4240343333330BB9524099999999F99E42406866666606B852409999999999A442406866666626B5524033333333B3AD42409A999999C1AE5240666666667EB242403433333333AA524099999999F1B04240CECCCCCC8CA1524033333333A3B242409A999999799C52409999999999B542406866666656965240CCCCCCCC2CB54240686666669E905240CCCCCCCCACAF424068666666068D5240333333332BAA42409A999999B18A52409999999979A842409A999999F9845240666666663EA442409A999999B97C524033333333AB9D42409A999999F96F524033333333A39E424034333333D3695240333333337BA142409A999999296852406666666646A542406866666686695240333333332BAA424000000000E86D52409999999919B0424068666666F66E52409999999999B54240686666661E6E52409999999919B74240686666660E6A524066666666F6B74240CECCCCCC7C6852400000000018B9424034333333B36652400000000060BC424068666666CE5E5240333333332BBB42409A999999815852409999999949B4424034333333834D5240666666663EA242400000000050395240333333331B964240343333337330524000000000B883424034333333132A524000000000D07D424068666666F6165240CCCCCCCC4473424034333333D3095240333333331B6242409A99999949FC514066666666DE584240CECCCCCC54F35140666666668E57424068666666F6EE5140CCCCCCCC345942409A99999999EA514000000000D05D4240CECCCCCC3CE65140CCCCCCCC2C6C42409A999999F9E1514066666666EE8142403433333333DE51403333333353904240CECCCCCCB4DB514033333333CBA24240343333331BDD514000000000D0B7424034333333B3DE5140CCCCCCCC2CCD42403433333353E0514000000000D8E54240CECCCCCCF4E2514000000000A0EE4240CECCCCCC24E55140666666667EF442403433333343E551409999999971F742403433333353E351400000000048F742400000000038DF51409999999901F4424000000000F0D851400000000070F342409A99999979D45140666666668EF5424034333333D3D1514033333333030143409A99999919D2514033333333CB154340343333334BD55140333333334B2743400000000060D05140CCCCCCCC7C3543406866666656C35140333333336B3A43400000000040B8514066666666163643409A99999919AF514066666666CE2A43409A99999969A7514033333333931843400000000030A1514000000000A8094340CECCCCCCBC9A5140666666660EFE4240CECCCCCC0C9451409999999979F8424000000000488F51403333333353F64240CECCCCCCBC8D51409999999969F1424034333333C38C514000000000F8E142409A999999519051403333333303D542400000000018905140666666668ECA424034333333138C51409999999991C5424034333333AB875140333333330BC64240CECCCCCCDC8251400000000078C842409A999999097F514066666666D6CC424034333333337C51406666666606CE42409A999999897451409999999909CC4240CECCCCCC0C68514033333333CBC64240686666667E5F5140CCCCCCCC4CBE424034333333E35A5140CCCCCCCC1CB34240CECCCCCC8C595140333333333BA5424000000000805B514000000000989A424068666666865A5140CCCCCCCC34934240CECCCCCCA456514000000000F88E4240343333337353514000000000E08D424034333333F3505140333333334394424000000000884B5140CCCCCCCC1CA242403433333333435140333333339BA9424000000000783D514066666666BEAA4240343333335B3A514066666666FEA9424000000000A8385140666666668EA8424068666666BE36514033333333C3A642409A999999A935514066666666A6A2424000000000B83451406666666606A14240CECCCCCC0C325140666666664EA242409A999999492E51403333333313A1424034333333D32A514033333333BB9C4240CECCCCCCC4285140333333337B9742409A999999F9225140999999999991424034333333C318514099999999518B4240343333332B13514066666666A68442409A99999939125140CCCCCCCCAC81424034333333B310514099999999C182424034333333930D514033333333937942406866666656045140333333336B7C42400000000050FD504000000000388842400000000068F5504000000000F09142406866666606F15040333333330B9642403433333393F0504033333333939942400000000030F0504066666666169D4240CECCCCCCCCEC5040333333337B9C424000000000E0E6504099999999299E42409A999999F9E250409999999921A24240343333331BE150406666666606A14240CECCCCCC44DC504033333333D39A42406866666676D45040333333331B9E42403433333383CC504033333333DBAA42400000000068C450406666666686AF42409A999999F9B45040333333339BAC4240CECCCCCC6CA150400000000020AC424034333333339E50400000000020AF4240343333336B9650406666

Einen sehr einfachen Filter auf ein Feld zu bauen ist keine große Aufgabe, das ist schlicht und einfach eine WHERE Abfrage im Select Befehl. Möchten wir beispielsweise die zurückgegebenen Länder auf alle Länder filtern die in der Region `Americas` sind können wir dazu den folgenden Befehl nutzen:

In [2]:
DECLARE @pRegion nvarchar(30) = N'Americas';

SELECT
	  CountryName
	, Continent
	, Region
	, Subregion
FROM  Application.Countries
WHERE Region = @pRegion;

(35 rows affected)

Total execution time: 00:00:00.051

CountryName Continent Region Subregion Antigua and Barb. North America Americas Caribbean Argentina South America Americas South America Bahamas North America Americas Caribbean Barbados North America Americas Caribbean Belize North America Americas Central America Bolivia South America Americas South America Brazil South America Americas South America Canada North America Americas Northern America Chile South America Americas South America Colombia South America Americas South America Costa Rica North America Americas Central America Cuba North America Americas Caribbean Dominica North America Americas Caribbean Dominican Rep. North America Americas Caribbean Ecuador South America Americas South America El Salvador North America Americas Central America Grenada North America Americas Caribbean Guatemala North America Americas Central America Guyana South America Americas South America Haiti North America Americas Caribbean Honduras North America Americas Central America Jamaica North America Americas Caribbean Mexico North America Americas Central America Nicaragua North America Americas Central America Panama North America Americas Central America Paraguay South America Americas South America Peru South America Americas South America Saint Lucia North America Americas Caribbean St. Kitts and Nevis North America Americas Caribbean St. Vin. and Gren. North America Americas Caribbean Suriname South America Americas South America Trinidad and Tobago North America Americas Caribbean United States North America Americas Northern America Uruguay South America Americas South America Venezuela South America Americas South America

So weit, so einfach. Etwas kniffliger wird es, wenn wir diesen Filter nun ein- und ausschaltbar machen wollen. Wenn wir gar nicht filtern wollen dann können wir ja nicht irgendeinen Wert übergeben. Die Lösung ist aber eigentlich ganz einfach: Als "kein Filter" Wert übergeben wir einfach den Wert `NULL`. Wenn dieser Wert kommt soll die `WHERE` Klausel einfach das zu filternde Feld mit sich selbst vergleichen. Ein Wert mit sich selbst verglichen liefert immer das Ergebnis `TRUE` zurück und somit ist die Bedingung immer erfüllt. Ein solches Verhalten können wir durch die Funktion `ISNULL` erzielen. Was ISNULL genau macht findet ihr [hier](https://docs.microsoft.com/de-de/sql/t-sql/functions/isnull-transact-sql?view=sql-server-ver15). Kurz gesagt: ISNULL überprüft ob der erste Parameter NULL ist. Ist das der Fall wird der Wert des zweiten Parameters zurückgegeben, ansonsten der des ersten. Das ist doch genau das, was wir brauchen. Der Trick ist, dass wir die Funktion `ISNULL` nicht auf die Spalte sondern auf den übergebenen Parameter anwenden. Übergeben wir einen Wert wie im Beispiel zuvor, so funktioniert der Filter genau wie zuvor:

In [ ]:
DECLARE @pRegion nvarchar(30) = N'Americas';

SELECT
	  CountryName
	, Continent
	, Region
	, Subregion
FROM  Application.Countries
WHERE Region = ISNULL(@pRegion, Region);

Setzen wir den Parameter allerdings auf `NULL` so wird nicht mehr gefiltert. Wir bekommen 190 Datensätze zurückgeliefert, genau wie beim allerersten SQL Befehl ganz oben:

In [4]:
DECLARE @pRegion nvarchar(30) = NULL;

SELECT
	  CountryName
	, Continent
	, Region
	, Subregion
FROM  Application.Countries
WHERE Region = ISNULL(@pRegion, Region);


(190 rows affected)

Total execution time: 00:00:00.055

CountryName Continent Region Subregion Afghanistan Asia Asia Southern Asia Albania Europe Europe Southern Europe Algeria Africa Africa Northern Africa Andorra Europe Europe Southern Europe Angola Africa Africa Middle Africa Antigua and Barb. North America Americas Caribbean Argentina South America Americas South America Armenia Asia Asia Western Asia Australia Oceania Oceania Australia and New Zealand Austria Europe Europe Western Europe Azerbaijan Asia Asia Western Asia Bahamas North America Americas Caribbean Bahrain Asia Asia Western Asia Bangladesh Asia Asia Southern Asia Barbados North America Americas Caribbean Belarus Europe Europe Eastern Europe Belgium Europe Europe Western Europe Belize North America Americas Central America Benin Africa Africa Western Africa Bhutan Asia Asia Southern Asia Bolivia South America Americas South America Bosnia and Herz. Europe Europe Southern Europe Botswana Africa Africa Southern Africa Brazil South America Americas South America Brunei Asia Asia South-Eastern Asia Bulgaria Europe Europe Eastern Europe Burkina Faso Africa Africa Western Africa Burundi Africa Africa Eastern Africa Cambodia Asia Asia South-Eastern Asia Cameroon Africa Africa Middle Africa Canada North America Americas Northern America Central African Rep. Africa Africa Middle Africa Chad Africa Africa Middle Africa Chile South America Americas South America China Asia Asia Eastern Asia Colombia South America Americas South America Comoros Africa Africa Eastern Africa Congo Africa Africa Middle Africa Costa Rica North America Americas Central America Côte d'Ivoire Africa Africa Western Africa Croatia Europe Europe Southern Europe Cuba North America Americas Caribbean Cyprus Asia Asia Western Asia Czech Rep. Europe Europe Eastern Europe Dem. Rep. Congo Africa Africa Middle Africa Dem. Rep. Korea Asia Asia Eastern Asia Denmark Europe Europe Northern Europe Djibouti Africa Africa Eastern Africa Dominica North America Americas Caribbean Dominican Rep. North America Americas Caribbean Ecuador South America Americas South America Egypt Africa Africa Northern Africa El Salvador North America Americas Central America Eq. Guinea Africa Africa Middle Africa Eritrea Africa Africa Eastern Africa Estonia Europe Europe Northern Europe Ethiopia Africa Africa Eastern Africa Fiji Oceania Oceania Melanesia Finland Europe Europe Northern Europe France Europe Europe Western Europe Gabon Africa Africa Middle Africa Gambia Africa Africa Western Africa Georgia Asia Asia Western Asia Germany Europe Europe Western Europe Ghana Africa Africa Western Africa Greece Europe Europe Southern Europe Grenada North America Americas Caribbean Guatemala North America Americas Central America Guinea Africa Africa Western Africa Guinea-Bissau Africa Africa Western Africa Guyana South America Americas South America Haiti North America Americas Caribbean Honduras North America Americas Central America Hungary Europe Europe Eastern Europe Iceland Europe Europe Northern Europe India Asia Asia Southern Asia Indonesia Asia Asia South-Eastern Asia Iran Asia Asia Southern Asia Iraq Asia Asia Western Asia Ireland Europe Europe Northern Europe Israel Asia Asia Western Asia Italy Europe Europe Southern Europe Jamaica North America Americas Caribbean Japan Asia Asia Eastern Asia Jordan Asia Asia Western Asia Kazakhstan Asia Asia Central Asia Kenya Africa Africa Eastern Africa Kiribati Oceania Oceania Micronesia Korea Asia Asia Eastern Asia Kuwait Asia Asia Western Asia Kyrgyzstan Asia Asia Central Asia Lao PDR Asia Asia South-Eastern Asia Latvia Europe Europe Northern Europe Lebanon Asia Asia Western Asia Lesotho Africa Africa Southern Africa Liberia Africa Africa Western Africa Libya Africa Africa Northern Africa Liechtenstein Europe Europe Western Europe Lithuania Europe Europe Northern Europe Luxembourg Europe Europe Western Europe Macedonia Europe Europe Southern Europe Madagascar Africa Africa Eastern Africa Malawi Africa Africa Eastern Africa Malaysia Asia Asia Sout

Was für einen Parameter und eine Spalte funktioniert funktioniert natürlich genau so für mehr als eine Spalte und einen Parameter. Im Beispiel haben wir alle Bedingungen mit einem `AND` miteinander verknüpft, weil das die von uns gewünschte Funktionalität ist: Je mehr Filter wir in den Comboboxen setzen desto mehr Werte werden herausgefiltert. Ohne jegliche Filterung liefert uns der Befehl wieder 190 Datensätze zurück.

In [5]:
DECLARE
	@pRegion nvarchar(30) = NULL
  , @pSubRegion nvarchar(30) = NULL
  , @pContinent nvarchar(30) = NULL
  , @pCountryName nvarchar(30) = NULL;

SELECT
	  CountryName
	, Continent
	, Region
	, Subregion
FROM  Application.Countries
WHERE Region = ISNULL (@pRegion, Region)
	  AND Subregion = ISNULL (@pSubRegion, Subregion)
	  AND Continent = ISNULL (@pContinent, Continent)
	  AND CountryName = ISNULL (@pCountryName, CountryName);


(190 rows affected)

Total execution time: 00:00:00.052

CountryName Continent Region Subregion Afghanistan Asia Asia Southern Asia Albania Europe Europe Southern Europe Algeria Africa Africa Northern Africa Andorra Europe Europe Southern Europe Angola Africa Africa Middle Africa Antigua and Barb. North America Americas Caribbean Argentina South America Americas South America Armenia Asia Asia Western Asia Australia Oceania Oceania Australia and New Zealand Austria Europe Europe Western Europe Azerbaijan Asia Asia Western Asia Bahamas North America Americas Caribbean Bahrain Asia Asia Western Asia Bangladesh Asia Asia Southern Asia Barbados North America Americas Caribbean Belarus Europe Europe Eastern Europe Belgium Europe Europe Western Europe Belize North America Americas Central America Benin Africa Africa Western Africa Bhutan Asia Asia Southern Asia Bolivia South America Americas South America Bosnia and Herz. Europe Europe Southern Europe Botswana Africa Africa Southern Africa Brazil South America Americas South America Brunei Asia Asia South-Eastern Asia Bulgaria Europe Europe Eastern Europe Burkina Faso Africa Africa Western Africa Burundi Africa Africa Eastern Africa Cambodia Asia Asia South-Eastern Asia Cameroon Africa Africa Middle Africa Canada North America Americas Northern America Central African Rep. Africa Africa Middle Africa Chad Africa Africa Middle Africa Chile South America Americas South America China Asia Asia Eastern Asia Colombia South America Americas South America Comoros Africa Africa Eastern Africa Congo Africa Africa Middle Africa Costa Rica North America Americas Central America Côte d'Ivoire Africa Africa Western Africa Croatia Europe Europe Southern Europe Cuba North America Americas Caribbean Cyprus Asia Asia Western Asia Czech Rep. Europe Europe Eastern Europe Dem. Rep. Congo Africa Africa Middle Africa Dem. Rep. Korea Asia Asia Eastern Asia Denmark Europe Europe Northern Europe Djibouti Africa Africa Eastern Africa Dominica North America Americas Caribbean Dominican Rep. North America Americas Caribbean Ecuador South America Americas South America Egypt Africa Africa Northern Africa El Salvador North America Americas Central America Eq. Guinea Africa Africa Middle Africa Eritrea Africa Africa Eastern Africa Estonia Europe Europe Northern Europe Ethiopia Africa Africa Eastern Africa Fiji Oceania Oceania Melanesia Finland Europe Europe Northern Europe France Europe Europe Western Europe Gabon Africa Africa Middle Africa Gambia Africa Africa Western Africa Georgia Asia Asia Western Asia Germany Europe Europe Western Europe Ghana Africa Africa Western Africa Greece Europe Europe Southern Europe Grenada North America Americas Caribbean Guatemala North America Americas Central America Guinea Africa Africa Western Africa Guinea-Bissau Africa Africa Western Africa Guyana South America Americas South America Haiti North America Americas Caribbean Honduras North America Americas Central America Hungary Europe Europe Eastern Europe Iceland Europe Europe Northern Europe India Asia Asia Southern Asia Indonesia Asia Asia South-Eastern Asia Iran Asia Asia Southern Asia Iraq Asia Asia Western Asia Ireland Europe Europe Northern Europe Israel Asia Asia Western Asia Italy Europe Europe Southern Europe Jamaica North America Americas Caribbean Japan Asia Asia Eastern Asia Jordan Asia Asia Western Asia Kazakhstan Asia Asia Central Asia Kenya Africa Africa Eastern Africa Kiribati Oceania Oceania Micronesia Korea Asia Asia Eastern Asia Kuwait Asia Asia Western Asia Kyrgyzstan Asia Asia Central Asia Lao PDR Asia Asia South-Eastern Asia Latvia Europe Europe Northern Europe Lebanon Asia Asia Western Asia Lesotho Africa Africa Southern Africa Liberia Africa Africa Western Africa Libya Africa Africa Northern Africa Liechtenstein Europe Europe Western Europe Lithuania Europe Europe Northern Europe Luxembourg Europe Europe Western Europe Macedonia Europe Europe Southern Europe Madagascar Africa Africa Eastern Africa Malawi Africa Africa Eastern Africa Malaysia Asia Asia Sout

Wenn wir nun Filterwerte in die Parameter setzen wird entsprechend gefiltert. Da die Felder `Continent`, `Region` und `Subregion` eine Hierarchie bilden ist egal ob wir auf die einzelnen Parameter filtern oder nur in `Subregion` auf `Caribbean`. Hätten wir aber Felder die keine Korelation haben wie in diesem Beispiel würde das auch funktionieren. 

In [ ]:
DECLARE
	@pRegion nvarchar(30) = 'Americas'
  , @pSubRegion nvarchar(30) = 'Caribbean'
  , @pContinent nvarchar(30) = 'North America'
  , @pCountryName nvarchar(30) = NULL;

SELECT
	  CountryName
	, Continent
	, Region
	, Subregion
FROM  Application.Countries
WHERE Region = ISNULL (@pRegion, Region)
	  AND Subregion = ISNULL (@pSubRegion, Subregion)
	  AND Continent = ISNULL (@pContinent, Continent)
	  AND CountryName = ISNULL (@pCountryName, CountryName);

So, damit sind wir mit unserem Filter fast soweit durch, die einzige Sache die jetzt noch fehlt ist, dass wir auch mehrere Werte in einem Feld filtern können. Um diese Funktion umzusetzen nutzen wir die Funktion [`TRIM`](https://docs.microsoft.com/de-de/sql/t-sql/functions/trim-transact-sql?view=sql-server-ver15) und [`STRING_SPLIT`](https://docs.microsoft.com/de-de/sql/t-sql/functions/string-split-transact-sql?view=sql-server-ver15) in Kombination mit dem Operator [`IN`](https://docs.microsoft.com/en-us/sql/t-sql/language-elements/in-transact-sql?view=sql-server-ver15#:~:text=IN%20%28Transact-SQL%29%201%20Syntax.%20To%20view%20Transact-SQL%20syntax,and%20Parallel%20Data%20Warehouse.%20...%208%20See%20Also). Das `TRIM` wird verwendet um eventuell vorhandene Leerzeichen am Anfang und am Ende des Textes zu löschen, mit `STRING_SPLIT` kann man einen Text der mit einem Trennzeichen getrennt wird in einzelne Zeilen eines Datasets verwandeln. Zu `STRING_SPLIT` hier ein kleines Beispiel:

In [7]:
SELECT
	 value
FROM STRING_SPLIT('Metallica,Megadeth,Slayer,Anthrax',',');

(4 rows affected)

Total execution time: 00:00:00.034

value Metallica Megadeth Slayer Anthrax

> WICHTIG: Die Funktion `STRING_SPLIT` gibt es erst seit der SQL Server Version 2016.

Das können wir uns nun für unseren Filter zunutze machen. Die Verbindung zu dem bisherigen Filter stellen wir über ein `OR` her. Das Beispiel liefert alle Länder in `Caribbean` und `Central America` zurück:


In [8]:
DECLARE
	@pRegion nvarchar(30) = N'Americas'
  , @pSubRegion nvarchar(30) = N'Caribbean,Central America'
  , @pContinent nvarchar(30) = N'North America'
  , @pCountryName nvarchar(30) = NULL;

SELECT
	  CountryName
	, Continent
	, Region
	, Subregion
FROM  Application.Countries
WHERE (
		  Region IN (
						SELECT
							 TRIM (value)
						FROM STRING_SPLIT(@pRegion, ',')
					)
		  OR Region = ISNULL (@pRegion, Region)
	  )
	  AND (
			  Subregion IN (
							   SELECT
									TRIM (value)
							   FROM STRING_SPLIT(@pSubRegion, ',')
						   )
			  OR Subregion = ISNULL (@pSubRegion, Subregion)
		  )
	  AND (
			  Continent IN (
							   SELECT
									TRIM (value)
							   FROM STRING_SPLIT(@pContinent, ',')
						   )
			  OR Continent = ISNULL (@pContinent, Continent)
		  )
	  AND (
			  CountryName IN (
								 SELECT
									  TRIM (value)
								 FROM STRING_SPLIT(@pCountryName, ',')
							 )
			  OR CountryName = ISNULL (@pCountryName, CountryName)
		  );

(21 rows affected)

Total execution time: 00:00:00.047

CountryName Continent Region Subregion Antigua and Barb. North America Americas Caribbean Bahamas North America Americas Caribbean Barbados North America Americas Caribbean Belize North America Americas Central America Costa Rica North America Americas Central America Cuba North America Americas Caribbean Dominica North America Americas Caribbean Dominican Rep. North America Americas Caribbean El Salvador North America Americas Central America Grenada North America Americas Caribbean Guatemala North America Americas Central America Haiti North America Americas Caribbean Honduras North America Americas Central America Jamaica North America Americas Caribbean Mexico North America Americas Central America Nicaragua North America Americas Central America Panama North America Americas Central America Saint Lucia North America Americas Caribbean St. Kitts and Nevis North America Americas Caribbean St. Vin. and Gren. North America Americas Caribbean Trinidad and Tobago North America Americas Caribbean

Sicherlich sind die Daten nicht unbedingt die geeignetsten Daten für dieses Beispiel, da es zwischen den Daten eine Abhängigkeit gibt aber ich denke dass zumindest die Idee wie das mit den Filtern funktioniert klar wird. Um das Beispiel abzuschliessen giessen wir das ganze jetzt noch in eine Stored Procedure die dann ganz bequem von der Frontend-Anwendung aufgerufen werden kann:

In [9]:
IF OBJECT_ID ('Application.filter_countries', 'P') IS NOT NULL
	DROP PROCEDURE Application.filter_countries;
GO

CREATE PROCEDURE Application.filter_countries
	@pRegion nvarchar(30) NULL
  , @pSubRegion nvarchar(30) NULL
  , @pContinent nvarchar(30) NULL
  , @pCountryName nvarchar(30) NULL
AS
SET NOCOUNT ON;

	BEGIN
		SELECT
			  CountryName
			, Continent
			, Region
			, Subregion
		FROM  Application.Countries
		WHERE (
				  Region IN (
								SELECT
									 TRIM (value)
								FROM STRING_SPLIT(@pRegion, ',')
							)
				  OR Region = ISNULL (@pRegion, Region)
			  )
			  AND (
					  Subregion IN (
									   SELECT
											TRIM (value)
									   FROM STRING_SPLIT(@pSubRegion, ',')
								   )
					  OR Subregion = ISNULL (@pSubRegion, Subregion)
				  )
			  AND (
					  Continent IN (
									   SELECT
											TRIM (value)
									   FROM STRING_SPLIT(@pContinent, ',')
								   )
					  OR Continent = ISNULL (@pContinent, Continent)
				  )
			  AND (
					  CountryName IN (
										 SELECT
											  TRIM (value)
										 FROM STRING_SPLIT(@pCountryName, ',')
									 )
					  OR CountryName = ISNULL (@pCountryName, CountryName)
				  );


	END;


Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.068

Diese Prozedur kann nun ganz einfach aufgerufen werden:

In [10]:
EXECUTE Application.filter_countries
	@pRegion = N'Americas'
  , @pSubRegion = N'Caribbean,Central America'
  , @pContinent = N'North America'
  , @pCountryName = NULL;
GO

Commands completed successfully.

Total execution time: 00:00:00.035

CountryName Continent Region Subregion Antigua and Barb. North America Americas Caribbean Bahamas North America Americas Caribbean Barbados North America Americas Caribbean Belize North America Americas Central America Costa Rica North America Americas Central America Cuba North America Americas Caribbean Dominica North America Americas Caribbean Dominican Rep. North America Americas Caribbean El Salvador North America Americas Central America Grenada North America Americas Caribbean Guatemala North America Americas Central America Haiti North America Americas Caribbean Honduras North America Americas Central America Jamaica North America Americas Caribbean Mexico North America Americas Central America Nicaragua North America Americas Central America Panama North America Americas Central America Saint Lucia North America Americas Caribbean St. Kitts and Nevis North America Americas Caribbean St. Vin. and Gren. North America Americas Caribbean Trinidad and Tobago North America Americas Caribbean

## Referenzen

- [TRIM](https://docs.microsoft.com/de-de/sql/t-sql/functions/trim-transact-sql?view=sql-server-ver15)
- [ISNULL](https://docs.microsoft.com/de-de/sql/t-sql/functions/isnull-transact-sql?view=sql-server-ver15)
- [STRING_SPLIT](https://docs.microsoft.com/de-de/sql/t-sql/functions/string-split-transact-sql?view=sql-server-ver15)